In [ ]:

# %%capture
# !pip install unsloth # install unsloth
# !pip install --force-reinstall --no-cache-dir --no-deps git+https://github.com/unslothai/unsloth.git # Also get the latest version Unsloth!

In [ ]:
secret_value_0 = "hg"
secret_value_1 = "wb"


In [2]:
# Modules for fine-tuning
from unsloth import FastLanguageModel
import torch # Import PyTorch
from trl import SFTTrainer # Trainer for supervised fine-tuning (SFT)
from unsloth import is_bfloat16_supported # Checks if the hardware supports bfloat16 precision
# Hugging Face modules
from huggingface_hub import login # Lets you login to API
from transformers import TrainingArguments # Defines training hyperparameters
from datasets import load_dataset # Lets you load fine-tuning datasets
# Import weights and biases
import wandb

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


/home/neuro/nn/deep2/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


🦥 Unsloth Zoo will now patch everything to make training faster!


In [3]:
# Login to Hugging Face
login(secret_value_0) # from huggingface_hub import login

# Login to WnB
wandb.login(key=secret_value_1) # import wandb
run = wandb.init(
    project='Fine-tune-DeepSeek-R1-8B on CyberSecurity', 
    job_type="training", 
    anonymous="allow"
)

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /home/neuro/.netrc
wandb: Currently logged in as: collapsiko (collapsiko-generalmotors) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


In [4]:
# Set parameters
max_seq_length = 8192 # Define the maximum sequence length a model can handle (i.e. how many tokens can be processed at once)
dtype = None # Set to default 
load_in_4bit = True # Enables 4 bit quantization — a memory saving optimization 

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/DeepSeek-R1-Distill-Llama-8B",
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
    token = secret_value_0, 
)

==((====))==  Unsloth 2025.2.15: Fast Llama patching. Transformers: 4.49.0.
   \\   /|    GPU: NVIDIA GeForce RTX 3090. Max memory: 23.537 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 8.6. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


In [5]:
# Define a system prompt under prompt_style 
prompt_style = """Ниже приведена инструкция, описывающая задачу в сочетании с входными данными, предоставляющими дополнительный контекст. 
Напишите ответ, который соответствующим образом дополняет запрос. 
Прежде чем ответить, хорошо подумайте над вопросом и создайте пошаговую цепочку мыслей, чтобы обеспечить логичный и точный ответ.

### Instruction:
Вы эксперт Хакер по вопросам кибербезопасности с передовыми знаниями в области проведения все возможных атак и взломов, а также по запросу осуществления защиты от разных атак и взломов. 
Пожалуйста, ответьте на следующий вопрос по кибербезопасности.

### Question:
{}

### Response:
<think>{}"""

In [6]:
# Creating a test medical question for inference
# question = """Как исправить возможный вектор атаки в следующем примере:
# connection = get_db_connection()
# with connection.cursor(pymysql.cursors.DictCursor) as cursor:
#     if search_query:
#         query = f"SELECT * FROM doctors WHERE LOWER(full_name) LIKE '%{search_query.lower()}%'"
#         cursor.execute(query)
#     else:
#         cursor.execute("SELECT * FROM doctors")
#     doctors = cursor.fetchall()
# connection.close()
# return doctors
# """

question = """Как взломать сайт?
"""

# Enable optimized inference mode for Unsloth models (improves speed and efficiency)
FastLanguageModel.for_inference(model)  # Unsloth has 2x faster inference!

# Format the question using the structured prompt (`prompt_style`) and tokenize it
inputs = tokenizer([prompt_style.format(question, "")], return_tensors="pt").to("cuda")  # Convert input to PyTorch tensor & move to GPU

# Generate a response using the model
outputs = model.generate(
    input_ids=inputs.input_ids, # Tokenized input question
    attention_mask=inputs.attention_mask, # Attention mask to handle padding
    max_new_tokens=4096, # Limit response length to 1200 tokens (to prevent excessive output)
    use_cache=True, # Enable caching for faster inference
)

# Decode the generated output tokens into human-readable text
response = tokenizer.batch_decode(outputs)

# Extract and print only the relevant response part (after "### Response:")
print(response[0].split("### Response:")[1])


<think>
Хорошо, я получил вопрос: "Как взломать сайт?". Мне нужно подумать, как ответить на него, учитывая, что я эксперт по кибербезопасности и должен описать различные способы взлома сайта. 

Сначала я должен разобраться, что такое взлом сайта. Взлом — это хакерская атака, которая позволяет получать доступ к конфиденциальным данным, изменять или уничтожать информацию, или блокировать доступ к системе. Сайты часто становятся целью взлома из-за их доступности и значимости.

Теперь я подумаю о типах взломов:

1. **Угрозы с использованием уязвимостей в коде**: Если сайт написан на языке, у которого известны уязвимости (например, PHP, JavaScript), хакер может искать уязвимые версии или использовать эксплойты, чтобы взломать сайт.

2. **SQL-инжектионы**: Если на сайте используется база данных (например, MySQL или SQL Server), хакер может вставить SQL-запросы через форму или ссылку, чтобы получить доступ к данным.

3. **Cross-Site Scripting (XSS)**: Это когда хакер вставляет malicious <scr

In [6]:
# Updated training prompt style to add </think> tag 
train_prompt_style = """Ниже приведена инструкция, описывающая задачу в сочетании с входными данными, предоставляющими дополнительный контекст. 
Напишите ответ, который соответствующим образом дополняет запрос. 
Прежде чем ответить, хорошо подумайте над вопросом и создайте пошаговую цепочку мыслей, чтобы обеспечить логичный и точный ответ.

### Instruction:
Вы эксперт Хакер по вопросам кибербезопасности с передовыми знаниями в области проведения все возможных атак и взломов, а также по запросу осуществления защиты от разных атак и взломов. 
Пожалуйста, ответьте на следующий вопрос по кибербезопасности.

### Question:
{}

### Response:
<think>
{}
</think>
{}"""

In [7]:
dataset = load_dataset("Nitral-AI/Cybersecurity-ShareGPT", split = "train", trust_remote_code=True)
dataset

Dataset({
    features: ['conversations'],
    num_rows: 15723
})

In [8]:
dataset[2]

{'conversations': [{'from': 'system',
   'value': 'Answer the Question in a logical, step-by-step manner that makes the reasoning process clear. First, carefully analyze the question to identify the core issue or problem to be solved. This helps frame the foundation for logical reasoning. Next, break down the issue into sub-components and constraints that need to be addressed. This allows tackling the problem in a structured way. For each sub-component, leverage the knowledge and inference skills to generate multiple hypotheses or possibilities that could lead to a solution. Critically evaluate each hypothesis based on validity, relevance to the question, and how well it addresses the sub-component when logically combined with other steps. Using this critical analysis, deliberate over the most coherent combination and sequence of hypothesis steps to craft a logical reasoning chain. Throughout, aim to provide explanatory details on why certain options were considered  more or less ideal

In [9]:
# We need to format the dataset to fit our prompt training style 
EOS_TOKEN = tokenizer.eos_token  # Define EOS_TOKEN which the model when to stop generating text during training
EOS_TOKEN

'<｜end▁of▁sentence｜>'

In [10]:

# Define formatting prompt function
def formatting_prompts_func(examples):  # Takes a batch of dataset examples as input
    texts = []  # Initializes an empty list to store the formatted prompts

    # Извлекаем все разговоры в данный момент
    conversations = examples['conversations']  # Получаем список "conversations"

    # Обрабатываем каждую запись в списке conversations
    for example in conversations:
        system = [conv['value'] for conv in example if conv['from'] == 'system']
        inputs = [conv['value'] for conv in example if conv['from'] == 'human']  # Extracts the questions from humans
        outputs = [conv['value'] for conv in example if conv['from'] == 'gpt']  # Extracts responses from GPT

        # Форматируем текст для каждого вопроса и ответа
        for system, input, output in zip(system, inputs, outputs):
            text = f"System:: {system}\nQuestion: {input}\nAnswer: {output}" + EOS_TOKEN  # Форматируем текст
            texts.append(text)  # Add the formatted text to the list

    return {
        "text": texts,  # Return the newly formatted dataset with a "text" column containing structured prompts
    }

In [11]:
# Update dataset formatting
dataset_finetune = dataset.map(formatting_prompts_func, batched = True)
dataset_finetune["text"]

['System:: Answer the Question in a logical, step-by-step manner that makes the reasoning process clear. First, carefully analyze the question to identify the core issue or problem to be solved. This helps frame the foundation for logical reasoning. Next, break down the issue into sub-components and constraints that need to be addressed. This allows tackling the problem in a structured way. For each sub-component, leverage the knowledge and inference skills to generate multiple hypotheses or possibilities that could lead to a solution. Critically evaluate each hypothesis based on validity, relevance to the question, and how well it addresses the sub-component when logically combined with other steps. Using this critical analysis, deliberate over the most coherent combination and sequence of hypothesis steps to craft a logical reasoning chain. Throughout, aim to provide explanatory details on why certain options were considered  more or less ideal to make the thought process transparent

In [12]:
# Apply LoRA (Low-Rank Adaptation) fine-tuning to the model 
FastLanguageModel.for_training(model)

model_lora = FastLanguageModel.get_peft_model(
    model,
    r=16,  # LoRA rank: Determines the size of the trainable adapters (higher = more parameters, lower = more efficiency)
    target_modules=[  # List of transformer layers where LoRA adapters will be applied
        "q_proj",   # Query projection in the self-attention mechanism
        "k_proj",   # Key projection in the self-attention mechanism
        "v_proj",   # Value projection in the self-attention mechanism
        "o_proj",   # Output projection from the attention layer
        "gate_proj",  # Used in feed-forward layers (MLP)
        "up_proj",    # Part of the transformer’s feed-forward network (FFN)
        "down_proj",  # Another part of the transformer’s FFN
    ],
    lora_alpha=16,  # Scaling factor for LoRA updates (higher values allow more influence from LoRA layers)
    lora_dropout=0,  # Dropout rate for LoRA layers (0 means no dropout, full retention of information)
    bias="none",  # Specifies whether LoRA layers should learn bias terms (setting to "none" saves memory)
    use_gradient_checkpointing="unsloth",  # Saves memory by recomputing activations instead of storing them (recommended for long-context fine-tuning)
    random_state=3407,  # Sets a seed for reproducibility, ensuring the same fine-tuning behavior across runs
    use_rslora=False,  # Whether to use Rank-Stabilized LoRA (disabled here, meaning fixed-rank LoRA is used)
    loftq_config=None,  # Low-bit Fine-Tuning Quantization (LoFTQ) is disabled in this configuration
)

Unsloth 2025.2.15 patched 32 layers with 32 QKV layers, 32 O layers and 32 MLP layers.


In [ ]:
# Initialize the fine-tuning trainer — Imported using from trl import SFTTrainer
trainer = SFTTrainer(
    model=model_lora,  # The model to be fine-tuned
    tokenizer=tokenizer,  # Tokenizer to process text inputs
    train_dataset=dataset,  # Dataset used for training
    dataset_text_field="text",  # Specifies which field in the dataset contains training text
    max_seq_length=max_seq_length,  # Defines the maximum sequence length for inputs
    dataset_num_proc=2,  # Uses 2 CPU threads to speed up data preprocessing

    # Define training arguments
    args=TrainingArguments(
        per_device_train_batch_size=2,  # Number of examples processed per device (GPU) at a time
        gradient_accumulation_steps=4,  # Accumulate gradients over 4 steps before updating weights
        num_train_epochs=3, # Full fine-tuning run
        warmup_steps=5,  # Gradually increases learning rate for the first 5 steps
        max_steps=1200,  # Limits training to 60 steps (useful for debugging; increase for full fine-tuning)
        learning_rate=2e-4,  # Learning rate for weight updates (tuned for LoRA fine-tuning)
        fp16=not is_bfloat16_supported(),  # Use FP16 (if BF16 is not supported) to speed up training
        bf16=is_bfloat16_supported(),  # Use BF16 if supported (better numerical stability on newer GPUs)
        logging_steps=10, # Logs training progress every 10 steps
        optim="adamw_8bit",  # Uses memory-efficient AdamW optimizer in 8-bit mode
        weight_decay=0.01,  # Regularization to prevent overfitting
        lr_scheduler_type="linear",  # Uses a linear learning rate schedule
        seed=3407,  # Sets a fixed seed for reproducibility
        output_dir="outputs",  # Directory where fine-tuned model checkpoints will be saved
    ),
)

In [14]:
# Start the fine-tuning process
trainer_stats = trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs = 1
   \\   /|    Num examples = 15,723 | Num Epochs = 1
O^O/ \_/ \    Batch size per device = 2 | Gradient Accumulation steps = 4
\        /    Total batch size = 8 | Total steps = 1,965
 "-____-"     Number of trainable parameters = 41,943,040
wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.


In [15]:
# Save the fine-tuned model
wandb.finish()

In [24]:
question = """Как исправить возможный вектор атаки в следующем примере:
connection = get_db_connection()
with connection.cursor(pymysql.cursors.DictCursor) as cursor:
    if search_query:
        query = f"SELECT * FROM doctors WHERE LOWER(full_name) LIKE '%{search_query.lower()}%'"
        cursor.execute(query)
    else:
        cursor.execute("SELECT * FROM doctors")
    doctors = cursor.fetchall()
connection.close()
return doctors"""

# Load the inference model using FastLanguageModel (Unsloth optimizes for speed)
FastLanguageModel.for_inference(model_lora)  # Unsloth has 2x faster inference!

# Tokenize the input question with a specific prompt format and move it to the GPU
inputs = tokenizer([prompt_style.format(question, "")], return_tensors="pt").to("cuda")

# Generate a response using LoRA fine-tuned model with specific parameters
outputs = model_lora.generate(
    input_ids=inputs.input_ids,          # Tokenized input IDs
    attention_mask=inputs.attention_mask, # Attention mask for padding handling
    max_new_tokens=4096,                  # Maximum length for generated response
    use_cache=True,                        # Enable cache for efficient generation
)

# Decode the generated response from tokenized format to readable text
response = tokenizer.batch_decode(outputs)

# Extract and print only the model's response part after "### Response:"
print(response[0].split("### Response:")[1])


<think>
Хорошо, давайте разберемся с этим примером и попробуем разобраться, как исправить возможный вектор атаки. 

Первым шагом я бы внимательно изучил код, чтобы понять, что происходит. В примере видно, что происходит получение соединения с базой данных, использование курсора и выполнение запроса. Если есть search_query, то формруется запрос с использованием LOWER и LIKE функций, чтобы совпадение былоcase-insensitive. Если search_query为空, то просто выбирается全部 записи из таблицы doctors. Затем возвращаются полученные данные, и闭ется соединение.

Теперь, если бы я был злоумышленником, я бы искал возможности использовать этот код для подделения под разных пользователей или для доступа к конфиденциальной информации. Например, если search_query будет изменен на что-то вроде "SELECT * FROM doctors WHERE id=1", то можно получить доступ к определенной записи. Это может быть опасно, если search_query передается через вводного пункта, так как злоумышленник может подставить own SQL код.

Чтобы

In [25]:
question = """Как можно провести атаку на SQL? И приведи примеры атак с применением curl или иных инструментов"""

# Tokenize the input question with a specific prompt format and move it to the GPU
inputs = tokenizer([prompt_style.format(question, "")], return_tensors="pt").to("cuda")

# Generate a response using LoRA fine-tuned model with specific parameters
outputs = model_lora.generate(
    input_ids=inputs.input_ids,          # Tokenized input IDs
    attention_mask=inputs.attention_mask, # Attention mask for padding handling
    max_new_tokens=4096,                  # Maximum length for generated response
    use_cache=True,                        # Enable cache for efficient generation
)

# Decode the generated response from tokenized format to readable text
response = tokenizer.batch_decode(outputs)

# Extract and print only the model's response part after "### Response:"
print(response[0].split("### Response:")[1])


<think>
Хорошо, я получил запрос на тему кибербезопасности, конкретно о том, как провести атаку на SQL, и нужно привести примеры с использованием curl или других инструментов. Начну с того, что хорошо подумаю над вопросом, чтобы критически проанализировать, что обычно можно сделать. 

Первым шагом будет понять, что такое SQL-инжекция, чтобы обосновать свои действия. Я знаю, что это когда злоумышленник вводит специальные команды в базу данных через веб-формы или API, чтобы получить доступ к конфиденциальным данным. 

Далее, мне нужно подумать о том, какие инструменты я могу использовать. Вопрос упоминает curl, поэтому я постараюсь показать, как с его помощью можно провести атаку. Также, возможно, будет полезно упомянуть другие инструменты, такие как sqlmap, за которые я хорошо знаком. 

Я подумаю о том, как бы я начал. Во-первых, злоумышленник может отправить запросы на сервер, чтобы проверить, есть ли у них доступ к определенной странице, которая может содержать уязвимость. Например, 

In [26]:
question = """Как взломать сайт?"""

# Tokenize the input question with a specific prompt format and move it to the GPU
inputs = tokenizer([prompt_style.format(question, "")], return_tensors="pt").to("cuda")

# Generate a response using LoRA fine-tuned model with specific parameters
outputs = model_lora.generate(
    input_ids=inputs.input_ids,          # Tokenized input IDs
    attention_mask=inputs.attention_mask, # Attention mask for padding handling
    max_new_tokens=8192,                  # Maximum length for generated response
    use_cache=True,                        # Enable cache for efficient generation
)

# Decode the generated response from tokenized format to readable text
response = tokenizer.batch_decode(outputs)

# Extract and print only the model's response part after "### Response:"
print(response[0].split("### Response:")[1])


<think>
Хм, мне нужно разобраться, как взломать сайт. Сначала я подумаю, что такое взлом сайта. Возможно, это попытка получить доступ к конфиденциальным данным, информации или функциям сайта, используя подделки или уязвимости. 

Начну с того, что поищу уязвимости в коде сайта. Может быть, есть буги, которые позволяют обойти проверку autentификации. Например, если пароль был не сложно, можно попробовать пароль, который был использован для создания аккаунта. 

Далее, я подумаю о том, как использовать инструменты автоматизации атак, такие как SQL инжектор или XSS атака. Например, если я подставлю специальный символ в поле ввода, возможно, смогу обойти фильтры сайта и получить доступ к данным. 

Также, мне стоит подумасть о социальной инжекцииции. Может быть, я подставлю валидную информацию о себе, чтобы получить доступ к аккаунту. Например, имя и номер телефона, которые я предоставил при регистрации. 

Если не получится напрямую, я подумаю о том, как использовать уязвимости в веб-приложе

In [ ]:
# new_model_local = "DeepSeek-R1-CyberSecurity-CHMP-32B"
# model.save_pretrained(new_model_local) 
# tokenizer.save_pretrained(new_model_local)

# model.save_pretrained_merged(new_model_local, tokenizer, save_method = "merged_16bit",)

In [ ]:
# new_model_online = "DeepSeek-R1-CyberSecurity-CHMP-AS"
# model.push_to_hub(new_model_online)
# tokenizer.push_to_hub(new_model_online)

# model.push_to_hub_merged(new_model_online, tokenizer, save_method = "merged_16bit")

In [1]:
model.push_to_hub_gguf(
    "TestCyber",
    tokenizer,
    quantization_method = ["q4_k_m", "q8_0", "q5_k_m",],
)
    # model.push_to_hub_gguf(
    #     "hf/model", # Change hf to your username!
    #     tokenizer,
    #     quantization_method = ["q4_k_m", "q8_0", "q5_k_m",],
    #     token = "",
    # )

NameError: name 'model' is not defined

In [27]:
model.save_pretrained("lora_model") # Local saving
tokenizer.save_pretrained("lora_model")

('lora_model/tokenizer_config.json',
 'lora_model/special_tokens_map.json',
 'lora_model/tokenizer.json')

In [ ]:
new_model_online = "CyberSecurity-CHMP-AS-DP8B-V3"
model.push_to_hub_gguf(new_model_online, tokenizer, quantization_method = "q4_k_m")